In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))

In [3]:
import json
from datasets.jester import make_dataset, load_annotation_data
from sklearn.metrics import accuracy_score, accuracy_score, balanced_accuracy_score
import numpy as np
import pickle
from sklearn.manifold import TSNE
import plotly.express as px
from sklearn.neighbors import NearestCentroid, KNeighborsClassifier
from sklearn.model_selection import train_test_split
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler, Normalizer
from sklearn.svm import SVC
from sklearn.neural_network import MLPClassifier

# Prepare embeddings

In [1]:
!python utils/jester_json.py 'annotation_Jester'

In [ ]:
!python utils/n_frames_jester.py ./datasets/jester/20bn-jester-v1

In [ ]:
!python main.py --root_path ./ \
    --video_path ./datasets/jester/20bn-jester-v1 \
    --annotation_path ./annotation_Jester/jester.json \
    --result_path ./results \
    --resume_path ./weights/jester_resnext_101_RGB_32.pth \
    --dataset jester \
    --train_crop random \
    --modality RGB \
    --n_classes 27 \
    --n_finetune_classes 27 \
    --model resnext \
    --model_depth 101 \
    --resnet_shortcut B \
    --resnext_cardinality 32 \
    --groups 3 \
    --width_mult 1 \
    --learning_rate 0.1 \
    --sample_duration 32 \
    --downsample 2 \
    --batch_size 32 \
    --n_threads 0 \
    --checkpoint 1 \
    --n_val_samples 1 \
    --no_train \
    --no_val \
    --test_subset train \
    --test \
    --no_fc 

In [ ]:
!python main.py --root_path ./ \
    --video_path ./datasets/jester/20bn-jester-v1 \
    --annotation_path ./annotation_Jester/jester.json \
    --result_path ./results \
    --resume_path ./weights/jester_resnext_101_RGB_32.pth \
    --dataset jester \
    --train_crop random \
    --modality RGB \
    --n_classes 27 \
    --n_finetune_classes 27 \
    --model resnext \
    --model_depth 101 \
    --resnet_shortcut B \
    --resnext_cardinality 32 \
    --groups 3 \
    --width_mult 1 \
    --learning_rate 0.1 \
    --sample_duration 32 \
    --downsample 2 \
    --batch_size 32 \
    --n_threads 0 \
    --checkpoint 1 \
    --n_val_samples 1 \
    --no_train \
    --no_val \
    --test_subset val \
    --test \
    --no_fc 

In [ ]:
!python main.py --root_path ./ \
    --video_path ./datasets/jester/20bn-jester-v1 \
    --annotation_path ./annotation_Jester/jester.json \
    --result_path ./results \
    --resume_path ./weights/jester_resnext_101_RGB_32.pth \
    --dataset jester \
    --train_crop random \
    --modality RGB \
    --n_classes 27 \
    --n_finetune_classes 27 \
    --model resnext \
    --model_depth 101 \
    --resnet_shortcut B \
    --resnext_cardinality 32 \
    --groups 3 \
    --width_mult 1 \
    --learning_rate 0.1 \
    --sample_duration 32 \
    --downsample 2 \
    --batch_size 32 \
    --n_threads 0 \
    --checkpoint 1 \
    --n_val_samples 1 \
    --no_train \
    --no_val \
    --test_subset val \
    --test 

# Check accuracy

In [4]:
with open('./results/val_resnext.json', 'r') as f:
    val_results_dict = json.load(f)

In [5]:
val_filtered_results_dict = {}
for x in val_results_dict['results']:
    val_filtered_results_dict[x] = val_results_dict['results'][x][0]['label']

In [6]:
annotation_data = load_annotation_data('./annotation_Jester/jester.json')

In [7]:
val_filtered_ytrue_dict = {}
for x in annotation_data['database']:
    idx_data = annotation_data['database'][x]
    if idx_data['subset'] == 'validation' and x in val_filtered_results_dict:
        val_filtered_ytrue_dict[x] = idx_data['annotations']['label']

In [8]:
print('val: ' + str(accuracy_score(list(val_filtered_ytrue_dict.values()), list(val_filtered_results_dict.values()))))

val: 0.650818341674557


# Feature Embedding representation

## Val

In [9]:
with open('./results/val_resnext.dump', 'rb') as f:
    emb_val_result_dict = pickle.load(f)

In [9]:
tsne = TSNE(n_components=2, random_state=0)
projections = tsne.fit_transform(list(emb_val_result_dict['results']['mean'].values()))

fig = px.scatter(
    projections, x=0, y=1,
    color=val_filtered_ytrue_dict.values(), labels={'color': 'gesture'}
)
fig.update_traces(marker_size=3)
fig.show()

tsne = TSNE(n_components=3, random_state=0)
projections = tsne.fit_transform(list(emb_val_result_dict['results']['mean'].values()))

fig = px.scatter_3d(
    projections, x=0, y=1, z=2,
    color=val_filtered_ytrue_dict.values(), labels={'color': 'gesture'}
)
fig.update_traces(marker_size=3)
fig.show()

# Compare different classification

In [10]:
with open('./results/train_resnext.dump', 'rb') as f:
    emb_train_result_dict = pickle.load(f)

In [11]:
X_train = []
y_train = []
dct = {}
for x in emb_train_result_dict['results']['mean']:
    dct[x] = {'emb' : emb_train_result_dict['results']['mean'][x], 
              'y': annotation_data['database'][x]['annotations']['label']}
    X_train.append(emb_train_result_dict['results']['mean'][x])
    y_train.append(annotation_data['database'][x]['annotations']['label'])

In [12]:
# with open('./results/train_resnext_with_class.dump', 'wb') as f:
#     pickle.dump(dct, f)

In [13]:
X_val = np.array(list(emb_val_result_dict['results']['mean'].values()))
y_val = np.array(list(val_filtered_ytrue_dict.values()))

## KNN classification

In [14]:
%%time
neigh = KNeighborsClassifier(n_neighbors=5)
neigh.fit(X_train, y_train)

pred = neigh.predict(X_val)
print(accuracy_score(y_val, pred))
print(balanced_accuracy_score(y_val, pred))

0.8891519004463682
0.8812314128840727
CPU times: user 5min 19s, sys: 23.3 s, total: 5min 42s
Wall time: 1min 48s


In [15]:
%%time
clf = NearestCentroid()
clf.fit(X_train, y_train)

pred = clf.predict(X_val)

print(accuracy_score(y_val, pred))
print(balanced_accuracy_score(y_val, pred))

centroids = clf.centroids_
classes = clf.classes_

neigh = KNeighborsClassifier(n_neighbors=5, weights='distance')
neigh.fit(centroids, classes)

pred = neigh.predict(X_val)

print(accuracy_score(y_val, pred))
print(balanced_accuracy_score(y_val, pred))

0.8652103340998242
0.8557410202402003
0.8652103340998242
0.8557410202402003
CPU times: user 2.2 s, sys: 714 ms, total: 2.91 s
Wall time: 1.95 s


## SVC

In [23]:
%%time
clf = make_pipeline(StandardScaler(), SVC(kernel='linear'))
clf.fit(X_train, y_train)

pred = clf.predict(X_val)

print(accuracy_score(y_val, pred))
print(balanced_accuracy_score(y_val, pred))

0.9032868930068985
0.8957129979658985
CPU times: user 27min 22s, sys: 14.5 s, total: 27min 36s
Wall time: 27min 45s


In [13]:
!pip install catboost

    100% |████████████████████████████████| 11.1MB 2.7MB/s eta 0:00:01
    100% |████████████████████████████████| 7.2MB 4.6MB/s ta 0:00:011
  Using cached https://files.pythonhosted.org/packages/f7/d2/e07d3ebb2bd7af696440ce7e754c59dd546ffe1bbe732c8ab68b9c834e61/cycler-0.10.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/0c/89/cdd752da48b66f31a0732902cd9800e6d232ce65f6cc4e83f9d9d2bd99aa/kiwisolver-1.3.1-cp38-cp38-macosx_10_9_x86_64.whl


In [16]:
from catboost import CatBoostClassifier
model = CatBoostClassifier(
    iterations=50,
    random_seed=63,
#     custom_loss=['Accuracy']
)
model.fit(
    X_train, y_train,
#     eval_set=(X_val, y_val),
    verbose=False,
    plot=True
)

MetricVisualizer(layout=Layout(align_self='stretch', height='500px'))

In [17]:
pred = model.predict(X_val)

print(accuracy_score(y_val, pred))
print(balanced_accuracy_score(y_val, pred))

0.8710942783714324
0.8636011085542691
